In [37]:
%matplotlib qt
import matplotlib.pyplot as plt
import numpy as np

from scipy import signal
from data.tools import zed
from vis.robot_dynamics import utils

In [40]:
# uri = '20200311T215136-vh6a_13@1583963911.01-1583963956.01'
# uri = '20200311T181540-vh6a_13@1583950642.26-1583950687.26'
# uri = '20200228T213402-vh6a_07@1582926607.00-1582926652.00'
uri = '20200310T231051-vh6a_13@1583882067.79-1583882112.79'
topics = ['/vehicle/raw_bdy_can1', '/vehicle/raw_bdy_can2']

In [41]:
data = utils.load_data(uri, topics=topics, print_not_found_can_frame_errors=False)

In [42]:
def plot_cmd_vs_actual_position(data):
    fig, ax = plt.subplots(2, 2, sharex='all', sharey='all')
    
    # NorthWest
    ax[0][0].plot(
        data['/vehicle/raw_bdy_can1/EMU_ASC1_raCmds'].META.message_time_ns/1e9,
        data['/vehicle/raw_bdy_can1/EMU_ASC1_raCmds'].EMU_ASC1_raPositionCmdWest,
        'k--',
        label='Command')
    ax[0][0].plot(
        data['/vehicle/raw_bdy_can1/ASC1_raStatus'].META.message_time_ns/1e9,
        data['/vehicle/raw_bdy_can1/ASC1_raStatus'].ASC1_raPositionWest,
        'k',
        label='Actual')
    
    # NorthEast
    ax[0][1].plot(
        data['/vehicle/raw_bdy_can1/EMU_ASC1_raCmds'].META.message_time_ns/1e9,
        data['/vehicle/raw_bdy_can1/EMU_ASC1_raCmds'].EMU_ASC1_raPositionCmdEast,
        'k--')
    ax[0][1].plot(
        data['/vehicle/raw_bdy_can1/ASC1_raStatus'].META.message_time_ns/1e9,
        data['/vehicle/raw_bdy_can1/ASC1_raStatus'].ASC1_raPositionEast,
        'k')
    
    # SouthWest
    ax[1][0].plot(
        data['/vehicle/raw_bdy_can2/EMU_ASC2_raCmds'].META.message_time_ns/1e9,
        data['/vehicle/raw_bdy_can2/EMU_ASC2_raCmds'].EMU_ASC2_raPositionCmdWest,
        'k--')
    ax[1][0].plot(
        data['/vehicle/raw_bdy_can2/ASC2_raStatus'].META.message_time_ns/1e9,
        data['/vehicle/raw_bdy_can2/ASC2_raStatus'].ASC2_raPositionWest,
        'k')
    
    # SouthEast
    ax[1][1].plot(
        data['/vehicle/raw_bdy_can2/EMU_ASC2_raCmds'].META.message_time_ns/1e9,
        data['/vehicle/raw_bdy_can2/EMU_ASC2_raCmds'].EMU_ASC2_raPositionCmdEast,
        'k--')
    ax[1][1].plot(
        data['/vehicle/raw_bdy_can2/ASC2_raStatus'].META.message_time_ns/1e9,
        data['/vehicle/raw_bdy_can2/ASC2_raStatus'].ASC2_raPositionEast,
        'k')
    
    ax[0][0].legend()
    ax[0][0].set_ylabel('raPosition (mm)')
    ax[0][0].set_title('NorthWest')
    ax[0][1].set_title('NorthEast')
    ax[1][0].set_ylabel('raPosition (mm)')
    ax[1][0].set_title('SouthWest')
    ax[1][0].set_xlabel('Time (s)')
    ax[1][1].set_xlabel('Time (s)')
    ax[1][1].set_title('SouthEast')
    for row in ax:
        for axis in row:
            axis.grid()
    fig.tight_layout()
    
    return fig, ax

def plot_cmd_position(data):
    fig, ax = plt.subplots()
    
    # NorthWest
    ax.plot(
        data['/vehicle/raw_bdy_can1/EMU_ASC1_raCmds'].META.message_time_ns/1e9,
        data['/vehicle/raw_bdy_can1/EMU_ASC1_raCmds'].EMU_ASC1_raPositionCmdWest,
        label='NorthWest')
    
    # NorthEast
    ax.plot(
        data['/vehicle/raw_bdy_can1/EMU_ASC1_raCmds'].META.message_time_ns/1e9,
        data['/vehicle/raw_bdy_can1/EMU_ASC1_raCmds'].EMU_ASC1_raPositionCmdEast,
        label='NorthEast')
    
    # SouthWest
    ax.plot(
        data['/vehicle/raw_bdy_can2/EMU_ASC2_raCmds'].META.message_time_ns/1e9,
        data['/vehicle/raw_bdy_can2/EMU_ASC2_raCmds'].EMU_ASC2_raPositionCmdWest,
        label='SouthWest')
    
    # SouthEast
    ax.plot(
        data['/vehicle/raw_bdy_can2/EMU_ASC2_raCmds'].META.message_time_ns/1e9,
        data['/vehicle/raw_bdy_can2/EMU_ASC2_raCmds'].EMU_ASC2_raPositionCmdEast,
        label='SouthEast')
    
    ax.set_ylabel('raPosition (mm)')
    ax.set_xlabel('Time (s)')
    ax.set_title('Commanded Position')
    ax.legend()
    ax.grid()
    
    return fig, ax
    
def plot_actual_position(data):
    fig, ax = plt.subplots()
    
    # NorthWest
    ax.plot(
        data['/vehicle/raw_bdy_can1/ASC1_raStatus'].META.message_time_ns/1e9,
        data['/vehicle/raw_bdy_can1/ASC1_raStatus'].ASC1_raPositionWest,
        label='NorthWest')
    
    # NorthEast
    ax.plot(
        data['/vehicle/raw_bdy_can1/ASC1_raStatus'].META.message_time_ns/1e9,
        data['/vehicle/raw_bdy_can1/ASC1_raStatus'].ASC1_raPositionEast,
        label='NorthEast')
    
    # SouthWest
    ax.plot(
        data['/vehicle/raw_bdy_can2/ASC2_raStatus'].META.message_time_ns/1e9,
        data['/vehicle/raw_bdy_can2/ASC2_raStatus'].ASC2_raPositionWest,
        label='SouthWest')
    
    # SouthEast
    ax.plot(
        data['/vehicle/raw_bdy_can2/ASC2_raStatus'].META.message_time_ns/1e9,
        data['/vehicle/raw_bdy_can2/ASC2_raStatus'].ASC2_raPositionEast,
        label='SouthEast')
    
    ax.set_ylabel('raPosition (mm)')
    ax.set_xlabel('Time (s)')
    ax.set_title('Actual Position')
    ax.legend()
    ax.grid()
    
    return fig, ax
    
def plot_pressure(data):
    fig, ax = plt.subplots()
    
    # NorthWest
    ax.plot(
        data['/vehicle/raw_bdy_can1/ASC1_raStatus'].META.message_time_ns/1e9,
        data['/vehicle/raw_bdy_can1/ASC1_raStatus'].ASC1_raPressureWest,
        label='NorthWest')
    
    # NorthEast
    ax.plot(
        data['/vehicle/raw_bdy_can1/ASC1_raStatus'].META.message_time_ns/1e9,
        data['/vehicle/raw_bdy_can1/ASC1_raStatus'].ASC1_raPressureEast,
        label='NorthEast')
    
    # SouthWest
    ax.plot(
        data['/vehicle/raw_bdy_can2/ASC2_raStatus'].META.message_time_ns/1e9,
        data['/vehicle/raw_bdy_can2/ASC2_raStatus'].ASC2_raPressureWest,
        label='SouthWest')
    
    # SouthEast
    ax.plot(
        data['/vehicle/raw_bdy_can2/ASC2_raStatus'].META.message_time_ns/1e9,
        data['/vehicle/raw_bdy_can2/ASC2_raStatus'].ASC2_raPressureEast,
        label='SouthEast')
    
    ax.set_ylabel('Pressure (Pa)')    
    ax.set_xlabel('Time (s)')
    ax.set_title('Strut Pressure')
    ax.legend()
    ax.grid()
    
    return fig, ax

def plot_strut_position(data):
    fig, ax = plt.subplots()
    
    # NorthWest
    ax.plot(
        data['/vehicle/raw_bdy_can1/ASC1_ecuStateStatus'].META.message_time_ns/1e9,
        data['/vehicle/raw_bdy_can1/ASC1_ecuStateStatus'].ASC1_strutHeightWest,        
        label='NorthWest')
    
    # NorthEast
    ax.plot(
        data['/vehicle/raw_bdy_can1/ASC1_ecuStateStatus'].META.message_time_ns/1e9,
        data['/vehicle/raw_bdy_can1/ASC1_ecuStateStatus'].ASC1_strutHeightEast,
        label='NorthEast')
    
    # SouthWest
    ax.plot(
        data['/vehicle/raw_bdy_can2/ASC2_raStatus'].META.message_time_ns/1e9,
        data['/vehicle/raw_bdy_can2/ASC2_ecuStateStatus'].ASC2_strutHeightWest,
        label='SouthWest')
    
    # SouthEast
    ax.plot(
        data['/vehicle/raw_bdy_can2/ASC2_ecuStateStatus'].META.message_time_ns/1e9,
        data['/vehicle/raw_bdy_can2/ASC2_ecuStateStatus'].ASC2_strutHeightEast,
        label='SouthEast')
    
    ax.set_ylabel('Position (mm)')    
    ax.set_xlabel('Time (s)')
    ax.set_title('Strut Position')
    ax.legend()
    ax.grid()
    
    return fig, ax

def calculate_velocity(data):
    dt = 0.005    
    t_north = data['/vehicle/raw_bdy_can1/ASC1_ecuStateStatus'].META.message_time_ns/1e9
    t_south = data['/vehicle/raw_bdy_can2/ASC2_ecuStateStatus'].META.message_time_ns/1e9
    t0 = t_north[0]
    t1 = t_north[-1]
    t_interp = np.arange(t0, t1, dt)    
    x_north_west = data['/vehicle/raw_bdy_can1/ASC1_ecuStateStatus'].ASC1_strutHeightWest
    x_north_east = data['/vehicle/raw_bdy_can1/ASC1_ecuStateStatus'].ASC1_strutHeightEast
    x_south_west = data['/vehicle/raw_bdy_can2/ASC2_ecuStateStatus'].ASC2_strutHeightWest
    x_south_east = data['/vehicle/raw_bdy_can2/ASC2_ecuStateStatus'].ASC2_strutHeightEast
    
    # interp        
    x_north_west = np.interp(t_interp, t_north, x_north_west)
    x_north_east = np.interp(t_interp, t_north, x_north_east)
    x_south_west = np.interp(t_interp, t_south, x_south_west)
    x_south_east = np.interp(t_interp, t_south, x_south_east)
    
    # filter
    f_sampling = 1.0/dt
    f_cutoff = 10 # Hz
    b, a = signal.butter(4, f_cutoff/(f_sampling/2), 'low')
    x_north_west = signal.filtfilt(b, a, x_north_west)
    x_north_east = signal.filtfilt(b, a, x_north_east)
    x_south_west = signal.filtfilt(b, a, x_south_west)
    x_south_east = signal.filtfilt(b, a, x_south_east)    
    
    # differentiation
    v_north_west = np.gradient(x_north_west, dt)
    v_north_east = np.gradient(x_north_east, dt)    
    v_south_west = np.gradient(x_south_west, dt)
    v_south_east = np.gradient(x_south_east, dt)
    return t_interp, v_north_west, v_north_east, v_south_west, v_south_east

def plot_strut_velocity(data):
    t, v_north_west, v_north_east, v_south_west, v_south_east = calculate_velocity(data)
    
    fig, ax = plt.subplots()
    
    ax.plot(t, v_north_west, label='NorthWest')
    ax.plot(t, v_north_east, label='NorthEast')
    ax.plot(t, v_south_west, label='SouthWest')
    ax.plot(t, v_south_east, label='SouthEast')
    
    ax.set_ylabel('Velocity (mm/s)')
    ax.set_xlabel('Time (s)')
    ax.set_title('Strut Velocity (mm/s)')
    ax.legend()
    ax.grid()
    
    return fig, ax
    

In [43]:
fig0, ax0 = plot_cmd_vs_actual_position(data)
fig0.suptitle(uri)

fig1, ax1 = plot_cmd_position(data)
fig1.suptitle(uri)

fig2, ax2 = plot_actual_position(data)
fig2.suptitle(uri)

fig3, ax3 = plot_pressure(data)
fig3.suptitle(uri)

fig4, ax4 = plot_strut_position(data)
fig4.suptitle(uri)

fig5, ax5 = plot_strut_velocity(data)
fig5.suptitle(uri)

ValueError: x and y must have same first dimension, but have shapes (4499,) and (4500,)